In [1]:
import numpy as np
import random

import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim

from matplotlib import pyplot as plt

from numpy import exp,arange
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

In [2]:
# ==========
# helping methods
# ==========

# generate a list from lower and upper bound
def gen_list(p0, pn, delta, dig=5):
    ret = []
    i = p0
    while i < pn:
        ret.append(float(i))
        i += delta
        i = round(i, dig)
    return ret

# padding and zero padding
def padding(origin, a_list, b_list):
    return np.hstack((a_list, origin, b_list))

def zero_padding(origin, num):
    zero_list = [0 for i in range(num)]
    return padding(origin, zero_list, zero_list)

# trainning pairs
def gen_pair(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-1-length)
        train = current_t[p-length:p+length+1]
        solu = next_t[p]
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

# trainning pairs (in average)
def gen_pair_ave(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-2-length)
        train0 = current_t[p-length-1:p+length+2]
        solu1 = next_t[p]
        solu2 = next_t[p+1]
        train = []
        for j, t in enumerate(train0):
            train.append(0.5 * (train0[j+1] + t))
        solu = 0.5 * (solu1 + solu2)
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

In [3]:
# the analytical representation of exact solution
def heat_equ_analytical_solu(x, t):
    return np.sin(np.pi * x) * np.exp(-np.power(np.pi, 2) * t)

In [4]:
# restnet
class ResNet(nn.Module):
    def __init__(self, i, h, o):
        super(ResNet, self).__init__()
        self.linear1 = nn.Linear(i, h)
        self.relu1 = nn.ReLU()
        self.linear2 = nn.Linear(h, o)
        self.relu2 = nn.ReLU()
        
    def forward(self, x):
        out = self.linear1(x)
        out = self.relu1(out)
        out = self.linear2(out)
        out = self.relu2(out)
        return out + torch.mean(x)

    def load_model(self, save_path):
        self.load_state_dict(torch.load(save_path))

    def save_model(self, save_path):
        torch.save(self.state_dict(), save_path)

## $\Delta x=\frac{1}{20}$

In [5]:
x_1 = arange(0, 2 * np.pi, 1/20)
t_1 = arange(0, 2 * np.pi, 1/20)
X_1,T_1 = meshgrid(x_1, t_1) # grid of point
Z_1 = heat_equ_analytical_solu(X_1, T_1) # evaluation of the function on the grid

In [6]:
# preparing the trainning set
data_pairs_1 = gen_pair(Z_1, len(Z_1[0]), len(Z_1), length=3, num=10000)
print(data_pairs_1)

[{'input': array([5.93410077e-18, 8.71804925e-18, 1.12873304e-17, 1.35786801e-17,
       1.55356775e-17, 1.71101350e-17, 1.82632843e-17]), 'solu': 8.289757356599697e-18}, {'input': array([9.44635252e-22, 9.81019749e-22, 9.93248283e-22, 9.81019749e-22,
       9.44635252e-22, 8.84990701e-22, 8.03554741e-22]), 'solu': 5.989106194626491e-22}, {'input': array([1.89483836e-20, 1.91845776e-20, 1.89483836e-20, 1.82456176e-20,
       1.70935838e-20, 1.55206493e-20, 1.35655449e-20]), 'solu': 1.113891349513784e-20}, {'input': array([0.00099903, 0.00098673, 0.00095014, 0.00089014, 0.00080823,
       0.00070642, 0.00058722]), 'solu': 0.0005434315349268492}, {'input': array([ 2.54757109e-19,  9.97182680e-34, -2.54757109e-19, -5.03241253e-19,
       -7.39333926e-19, -9.57221745e-19, -1.15153959e-18]), 'solu': -3.07227791001092e-19}, {'input': array([-7.14332580e-24, -7.05537960e-24, -6.79370655e-24, -6.36474989e-24,
       -5.77907197e-24, -5.05109411e-24, -4.19874156e-24]), 'solu': -3.88566723954520

In [7]:
model_1 = ResNet(7, 6, 1)
optimizer_1 = optim.Adam(model_1.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_1 = nn.MSELoss()
model_1.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [8]:
list_of_loss_1 = []
list_of_output_1 = []
for data in data_pairs_1:
    output = model_1(torch.FloatTensor(data["input"]))
    loss = criterion_1(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_1.append(np.log10(loss.item()))
    list_of_output_1.append(output)
    model_1.zero_grad()
    loss.backward()
    optimizer_1.step()

<ipython-input-8-ac38450c9edb>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_1.append(np.log10(loss.item()))


In [9]:
list_of_loss_1_file = open('list_of_loss_1.txt', 'w+')
for value in list_of_loss_1:
    list_of_loss_1_file.write(str(value)+" ")
list_of_loss_1_file.close()

list_of_output_1_file = open('list_of_output_1.txt', 'w+')
for value in list_of_output_1:
    list_of_output_1_file.write(str(value)+" ")
list_of_output_1_file.close()

In [26]:
model_1.save_model("model_1 delta x=1 20")

## $\Delta x=\frac{1}{40}$

In [10]:
x_2 = arange(0, 2 * np.pi, 1/40)
t_2 = arange(0, 2 * np.pi, 1/40)
X_2,T_2 = meshgrid(x_2, t_2) # grid of point
Z_2 = heat_equ_analytical_solu(X_2, T_2) # evaluation of the function on the grid

In [11]:
# preparing the trainning set
data_pairs_2 = gen_pair(Z_2, len(Z_2[0]), len(Z_2), length=3, num=10000)
print(data_pairs_2)

[{'input': array([1.31768494e-23, 1.96636617e-23, 2.60292410e-23, 3.22343414e-23,
       3.82407063e-23, 4.40113046e-23, 4.95105586e-23]), 'solu': 2.5186100560501e-23}, {'input': array([-4.05248983e-06, -4.17169850e-06, -4.26518726e-06, -4.33237972e-06,
       -4.37286163e-06, -4.38638338e-06, -4.37286163e-06]), 'solu': -3.3850777356299996e-06}, {'input': array([-0.23344536, -0.30901699, -0.38268343, -0.4539905 , -0.52249856,
       -0.58778525, -0.64944805]), 'solu': -0.3547226306995962}, {'input': array([-1.24402332e-17, -9.39791281e-18, -6.29765114e-18, -3.15856236e-18,
       -2.95806873e-32,  3.15856236e-18,  6.29765114e-18]), 'solu': -2.4679229011933248e-18}, {'input': array([3.34694757e-25, 3.59922853e-25, 3.82931905e-25, 4.03580054e-25,
       4.21739998e-25, 4.37299774e-25, 4.50163453e-25]), 'solu': 3.153347449487083e-25}, {'input': array([ 1.21286394e-25,  6.08307180e-26,  9.49490220e-41, -6.08307180e-26,
       -1.21286394e-25, -1.80994300e-25, -2.39586315e-25]), 'solu': -4.

In [12]:
model_2 = ResNet(7, 6, 1)
optimizer_2 = optim.Adam(model_2.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_2 = nn.MSELoss()
model_2.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [13]:
list_of_loss_2 = []
list_of_output_2 = []
for data in data_pairs_2:
    output = model_2(torch.FloatTensor(data["input"]))
    loss = criterion_2(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_2.append(np.log10(loss.item()))
    list_of_output_2.append(output)
    model_2.zero_grad()
    loss.backward()
    optimizer_2.step()

<ipython-input-13-de329c128c88>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_2.append(np.log10(loss.item()))


In [14]:
list_of_loss_2_file = open('list_of_loss_2.txt', 'w+')
for value in list_of_loss_2:
    list_of_loss_2_file.write(str(value)+" ")
list_of_loss_2_file.close()

list_of_output_2_file = open('list_of_output_2.txt', 'w+')
for value in list_of_output_2:
    list_of_output_2_file.write(str(value)+" ")
list_of_output_2_file.close()

In [27]:
model_2.save_model("model_1 delta x=1 40")

## $\Delta x=\frac{1}{80}$

In [15]:
x_3 = arange(0, 2 * np.pi, 1/80)
t_3 = arange(0, 2 * np.pi, 1/80)
X_3,T_3 = meshgrid(x_3, t_3) # grid of point
Z_3 = heat_equ_analytical_solu(X_3, T_3) # evaluation of the function on the grid

In [16]:
# preparing the trainning set
data_pairs_3 = gen_pair(Z_3, len(Z_3[0]), len(Z_3), length=3, num=10000)
print(data_pairs_3)

[{'input': array([-6.42456434e-05, -8.01615800e-19,  6.42456434e-05,  1.28392225e-04,
        1.92340834e-04,  2.55992869e-04,  3.19250180e-04]), 'solu': 0.00011349057328473434}, {'input': array([-7.77318310e-09, -1.03455901e-08, -1.29020450e-08, -1.54386059e-08,
       -1.79513615e-08, -2.04364375e-08, -2.28900020e-08]), 'solu': -1.3646747202999068e-08}, {'input': array([-1.17945115e-14, -1.14203789e-14, -1.10286369e-14, -1.06198895e-14,
       -1.01947670e-14, -9.75392500e-15, -9.29804311e-15]), 'solu': -9.387307924455793e-15}, {'input': array([-6.55145445e-23, -4.92245047e-23, -3.28585642e-23, -1.64419583e-23,
       -3.07728264e-37,  1.64419583e-23,  3.28585642e-23]), 'solu': -1.4533646991306298e-23}, {'input': array([-4.35340885e-27, -4.35676777e-27, -4.35340885e-27, -4.34333730e-27,
       -4.32656864e-27, -4.30312872e-27, -4.27305369e-27]), 'solu': -3.839234361355861e-27}, {'input': array([9.86214898e-22, 1.06944173e-21, 1.15101956e-21, 1.23082261e-21,
       1.30872781e-21, 1.3

In [17]:
model_3 = ResNet(7, 6, 1)
optimizer_3 = optim.Adam(model_3.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_3 = nn.MSELoss()
model_3.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [18]:
list_of_loss_3 = []
list_of_output_3 = []
for data in data_pairs_3:
    output = model_3(torch.FloatTensor(data["input"]))
    loss = criterion_3(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_3.append(np.log10(loss.item()))
    list_of_output_3.append(output)
    model_3.zero_grad()
    loss.backward()
    optimizer_3.step()

<ipython-input-18-3f959fb14d49>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_3.append(np.log10(loss.item()))


In [19]:
list_of_loss_3_file = open('list_of_loss_3.txt', 'w+')
for value in list_of_loss_3:
    list_of_loss_3_file.write(str(value)+" ")
list_of_loss_3_file.close()

list_of_output_3_file = open('list_of_output_3.txt', 'w+')
for value in list_of_output_3:
    list_of_output_3_file.write(str(value)+" ")
list_of_output_3_file.close()

In [29]:
model_3.save_model("model_1 delta x=1 80")

## $\Delta x=\frac{1}{160}$

In [20]:
x_4 = arange(0, 2 * np.pi, 1/160)
t_4 = arange(0, 2 * np.pi, 1/160)
X_4,T_4 = meshgrid(x_4, t_4) # grid of point
Z_4 = heat_equ_analytical_solu(X_4, T_4) # evaluation of the function on the grid

In [21]:
# preparing the trainning set
data_pairs_4 = gen_pair(Z_4, len(Z_4[0]), len(Z_4), length=3, num=10000)
print(data_pairs_4)

[{'input': array([-1.69296843e-08, -1.59678823e-08, -1.49999244e-08, -1.40261838e-08,
       -1.30470358e-08, -1.20628579e-08, -1.10740296e-08]), 'solu': -1.318712304296486e-08}, {'input': array([1.12865423e-23, 1.11485722e-23, 1.10063042e-23, 1.08597929e-23,
       1.07090951e-23, 1.05542686e-23, 1.03953733e-23]), 'solu': 1.021014894571461e-23}, {'input': array([-1.43811834e-21, -1.43784113e-21, -1.43700961e-21, -1.43562408e-21,
       -1.43368510e-21, -1.43119341e-21, -1.42814996e-21]), 'solu': -1.3497435743201817e-21}, {'input': array([5.76211256e-23, 5.80528069e-23, 5.84621078e-23, 5.88488704e-23,
       5.92129456e-23, 5.95541931e-23, 5.98724814e-23]), 'solu': 5.532847038867999e-23}, {'input': array([-2.10837342e-18, -2.09451691e-18, -2.07985292e-18, -2.06438711e-18,
       -2.04812544e-18, -2.03107418e-18, -2.01323990e-18]), 'solu': -1.9408933474351633e-18}, {'input': array([2.53865265e-22, 2.64628140e-22, 2.75288996e-22, 2.85843722e-22,
       2.96288250e-22, 3.06618554e-22, 3.1

In [22]:
model_4 = ResNet(7, 6, 1)
optimizer_4 = optim.Adam(model_4.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_4 = nn.MSELoss()
model_4.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [23]:
list_of_loss_4 = []
list_of_output_4 = []
for data in data_pairs_4:
    output = model_4(torch.FloatTensor(data["input"]))
    loss = criterion_4(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_4.append(np.log10(loss.item()))
    list_of_output_4.append(output)
    model_4.zero_grad()
    loss.backward()
    optimizer_4.step()

<ipython-input-23-f52da78e2a74>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_4.append(np.log10(loss.item()))


In [24]:
list_of_loss_4_file = open('list_of_loss_4.txt', 'w+')
for value in list_of_loss_4:
    list_of_loss_4_file.write(str(value)+" ")
list_of_loss_4_file.close()

list_of_output_4_file = open('list_of_output_4.txt', 'w+')
for value in list_of_output_4:
    list_of_output_4_file.write(str(value)+" ")
list_of_output_4_file.close()

In [30]:
model_4.save_model("model_1 delta x=1 160")